In [ ]:
import dgl
import numpy as np
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from ogb.nodeproppred import DglNodePropPredDataset

/usr/local/lib/python3.10/dist-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [19]:
dataset = DglNodePropPredDataset(name='ogbn-arxiv')
split_idx = dataset.get_idx_split()
train_idx, valid_idx, test_idx = split_idx["train"], split_idx["valid"], split_idx["test"]
graph, label = dataset[0]
label = label.squeeze().numpy()
years = graph.ndata.pop('year').squeeze().numpy()

In [3]:
papers = pd.read_csv('Arxiv.csv')
papers.head()

ID     mag_id                                              title  \
0   0    9657784  Title: evasion attacks against machine learnin...   
1   1   39886162  Title: how hard is computing parity with noisy...   
2   2  116214155  Title: on the absence of the rip in real world...   
3   3  121432379  Title: a promise theory perspective on data ne...   
4   4  231147053  Title: analysis of asymptotically optimal samp...   

                                            abstract  label_id     category  \
0  Abstract: In security-sensitive applications, ...         4  arxiv cs cr   
1  Abstract: We show a tight lower bound of $\Ome...         5  arxiv cs dc   
2  Abstract: The purpose of this paper is twofold...        28  arxiv cs it   
3  Abstract: Networking is undergoing a transform...         8  arxiv cs ni   
4  Abstract: Over the last 20 years significant e...        27  arxiv cs ro   

                                                text  
0  Title: evasion attacks against machine learnin...  
1  Title: how hard is computing parity with noisy...  
2  Title: on the absence of the rip in real world...  
3  Title: a promise theory perspective on data ne...  
4  Title: analysis of asymptotically optimal samp...

In [4]:
paper_id_map = dict(zip(papers['mag_id'].values.tolist(), papers['ID'].values.tolist()))
len(paper_id_map)

169343

## Paper-Author Links

In [5]:
authors = pd.read_csv('PAuAf_CS_20190919.tsv', sep='\t')
authors.head()

PaperSeqid  AuthorSeqid  AffiliationSeqid  AuthorSequenceNumber
0  1963479517   2167258348       134161618.0                     2
1  1963479517   2506097535       134161618.0                     3
2  1963479517   2296113232       142823887.0                     1
3  2095588566   2439736113               NaN                     2
4  2095588566   2575410839               NaN                     1

In [6]:
PaperSeqid = authors['PaperSeqid'].values
AuthorSeqid = authors['AuthorSeqid'].values

mask = np.isin(PaperSeqid, papers['mag_id'].values)
PaperSeqid = PaperSeqid[mask]
AuthorSeqid = AuthorSeqid[mask]

In [7]:
pa_pids = np.array([paper_id_map[_] for _ in PaperSeqid])

author_id_encoder = LabelEncoder()
pa_aids = author_id_encoder.fit_transform(AuthorSeqid).astype(np.int32)
assert pa_pids.shape[0] == pa_aids.shape[0]
print('Number of paper-author links', pa_aids.shape[0])

Number of paper-author links 300807


## Paper-FoS Links

In [8]:
FoSs = pd.read_csv('PF_CS_20190919.tsv', sep='\t')
FoSs.head()

PaperId  FieldOfStudyId
0  1963479517        41008148
1  1963479517        19417346
2  1963479517        56739046
3  1963479517        85973986
4  1963479517       206103860

In [9]:
PaperId = FoSs['PaperId'].values
FieldOfStudyId = FoSs['FieldOfStudyId'].values

mask = np.isin(PaperId, papers['mag_id'].values)
PaperId = PaperId[mask]
FieldOfStudyId = FieldOfStudyId[mask]

In [10]:
pf_pids = np.array([paper_id_map[_] for _ in PaperId])

fos_id_encoder = LabelEncoder()
pf_fids = fos_id_encoder.fit_transform(FieldOfStudyId).astype(np.int32)
assert pf_pids.shape[0] == pf_fids.shape[0]
print('Number of paper-fos links', pf_pids.shape[0])

Number of paper-fos links 755835


## Paper-Paper Links

In [11]:
graph = dgl.to_bidirected(graph)
src, dst = graph.edges()
mask = src < dst
src = src[mask].numpy()
dst = dst[mask].numpy()
src.shape[0]

1157799

In [12]:
paper_ids_with_author_fos = np.unique(np.concat((pa_pids, pf_pids)))
paper_ids_with_author_fos

array([     0,      1,      3, ..., 169186, 169187, 169188])

In [13]:
mask = np.isin(src, paper_ids_with_author_fos) & np.isin(dst, paper_ids_with_author_fos)
src = src[mask]
dst = dst[mask]
print('Number of paper-paper links', dst.shape[0])

Number of paper-paper links 468995


## Reset Id

In [14]:
paper_id_encoder = LabelEncoder()
paper_id_encoder.fit(paper_ids_with_author_fos)
print('Number of papers', len(paper_id_encoder.classes_))
paper_id_encoder.classes_

Number of papers 81634


array([     0,      1,      3, ..., 169186, 169187, 169188])

In [15]:
pa_pids = paper_id_encoder.transform(pa_pids).astype(np.int32)
pf_pids = paper_id_encoder.transform(pf_pids).astype(np.int32)
src = paper_id_encoder.transform(src).astype(np.int32)
dst = paper_id_encoder.transform(dst).astype(np.int32)

In [24]:
paper_labels = label[paper_id_encoder.classes_].astype(np.int8)

from collections import Counter
list(Counter(paper_labels).values())[-5:]

[110, 15, 24, 30, 26]

In [26]:
paper_years = years[paper_id_encoder.classes_].astype(np.int16)
paper_years.shape

(81634,)

In [ ]:
data = {
    'paper_labels': paper_labels,
    'paper_years': paper_years,
    'paper-paper': (src, dst),
    'paper-author': (pa_pids, pa_aids),
    'paper-fos': (pf_pids, pf_fids),
}

In [28]:
papers.set_index(keys='ID', inplace=True)
papers = papers.loc[paper_id_encoder.classes_]
papers.drop('text', inplace=True, axis=1)
papers.head()

mag_id                                              title  \
ID                                                                  
0      9657784  Title: evasion attacks against machine learnin...   
1     39886162  Title: how hard is computing parity with noisy...   
3    121432379  Title: a promise theory perspective on data ne...   
6   1444859417  Title: webvrgis based city bigdata 3d visualiz...   
7   1483430697  Title: information theoretic authentication an...   

                                             abstract  label_id     category  
ID                                                                            
0   Abstract: In security-sensitive applications, ...         4  arxiv cs cr  
1   Abstract: We show a tight lower bound of $\Ome...         5  arxiv cs dc  
3   Abstract: Networking is undergoing a transform...         8  arxiv cs ni  
6   Abstract: This paper shows the WEBVRGIS platfo...         6  arxiv cs hc  
7   Abstract: In the splitting model, information ...         4  arxiv cs cr

In [29]:
papers['title'] = papers['title'].str[7:]
papers['abstract'] = papers['abstract'].str[10:]
papers['category'] = papers['category'].apply(lambda x: f'cs.{x[-2:].upper()}')

def format_title(title):
    exceptions = {'is', 'are', 'with', 'and', 'the', 'a', 'an', 'but', 'for', 'nor', 'on', 'at', 'to', 'by', 'of', 'against', 'over', 'in', 'via'}
    words = title.split()
    formatted_words = [
        word.capitalize() if word not in exceptions or i == 0 else word
        for i, word in enumerate(words)
    ]
    return ' '.join(formatted_words)

papers['title'] = papers['title'].apply(format_title)
papers.head()

mag_id                                              title  \
ID                                                                  
0      9657784  Evasion Attacks against Machine Learning at Te...   
1     39886162  How Hard is Computing Parity with Noisy Commun...   
3    121432379      A Promise Theory Perspective on Data Networks   
6   1444859417  Webvrgis Based City Bigdata 3d Visualization a...   
7   1483430697  Information Theoretic Authentication and Secre...   

                                             abstract  label_id category  
ID                                                                        
0   In security-sensitive applications, the succes...         4    cs.CR  
1   We show a tight lower bound of $\Omega(N \log\...         5    cs.DC  
3   Networking is undergoing a transformation thro...         8    cs.NI  
6   This paper shows the WEBVRGIS platform overlyi...         6    cs.HC  
7   In the splitting model, information theoretic ...         4    cs.CR

In [ ]:
papers.reset_index(drop=True, inplace=True)
papers.to_csv('Paper.csv', index=False)

### Node Features

We generate embeddings as features for each node in the graph. Node embeddings are generated by passing the title and the abstract through a Sentence-BERT model and obtaining a 384-embedding vector for each movie node.


According to [Sentence-Transformers docs](https://www.sbert.net/docs/pretrained_models.html), the **all-MiniLM-L6-v2** model provides the best quality. So we use it to generate node features.

all-MiniLM-L6-v2

Description:	All-round model tuned for many use-cases. Trained on a large and diverse dataset of over 1 billion training pairs.
Base Model:	nreimers/MiniLM-L6-H384-uncased
Max Sequence Length:	256
Dimensions:	384
Normalized Embeddings:	true
Suitable Score Functions:	dot-product (util.dot_score), cosine-similarity (util.cos_sim), euclidean distance
Size:	80 MB
Pooling:	Mean Pooling
Training Data:	1B+ training pairs. For details, see model card.
Model Card:	https://huggingface.co/sentence-transformers/all-MiniLM-L6-v2


In [32]:
import torch
from sentence_transformers import SentenceTransformer

device = 'cuda:0' if torch.cuda.is_available() else 'cpu'
model = SentenceTransformer('../sentence-transformers/all-MiniLM-L6-v2', device=device)
model

SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [42]:
text = papers['title'] + ' ' + papers['abstract']

In [43]:
feats = model.encode(text, batch_size=4096, show_progress_bar=True, convert_to_numpy=True)

Batches: 100%|██████████| 20/20 [01:04<00:00,  3.22s/it]


In [44]:
data['paper_feats'] = feats
data

{'paper_labels': array([ 4,  5,  8, ..., 16, 30, 30], dtype=int8),
 'paper_years': array([2013, 2015, 2014, ..., 2019, 2019, 2019], dtype=int16),
 'paper-paper': (array([    0,     0,     0, ..., 81308, 81312, 81465], dtype=int32),
  array([  215,   347,   930, ..., 81577, 81345, 81519], dtype=int32)),
 'paper_author': (array([19239, 19239, 19239, ..., 35209, 53724, 53724], dtype=int32),
  array([127457,  19897, 127067, ...,  20462,  87283,   1618], dtype=int32)),
 'paper_fos': (array([19239, 19239, 19239, ..., 53724, 53724, 53724], dtype=int32),
  array([ 2826,  9870, 11927, ...,  2826, 14082,  8436], dtype=int32)),
 'paper_feats': array([[-0.09871526, -0.01083333, -0.05048474, ...,  0.01055331,
          0.03491311, -0.01338707],
        [-0.00965661, -0.05066415,  0.05266945, ...,  0.09849689,
         -0.06759875, -0.00852178],
        [-0.06771555, -0.02296721,  0.07591261, ..., -0.04729789,
          0.01239418, -0.02592889],
        ...,
        [-0.0010215 , -0.09171138,  0.020

In [ ]:
import pickle

with open('arxiv.pkl', 'wb') as f:
    pickle.dump(data, f)